In [39]:
import pandas as pd
import os
from Bio import SeqIO
from io import StringIO
import requests
import json

import seaborn as sns

In [11]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 20)
pd.set_option('display.max_rows', None) 

In [4]:
gene = 'PTPN11'

### Read in data

##### NSEuronet

In [9]:
# Manually load the NSEuronetData.csv (for all RAS genes)

df1 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\NSEuroNetData.csv", sep=';', header=None)
print(df1.head())

        0          1        2                3
0    KRAS    c.65A>G   p.Q22R  Noonan syndrome
1  PTPN11   c.922A>G  p.N308D  Noonan syndrome
2  PTPN11   c.184T>G   p.Y62D  Noonan syndrome
3  PTPN11   c.922A>G  p.N308D  Noonan syndrome
4  PTPN11  c.1232C>T  p.T411M  Noonan syndrome


In [8]:
# Filter column [2] with protein change pattern 

df1[2] = df1[2].astype(str).str.strip() # strip white space so everything is a string
NSEuronet_df = df1[df1[2].str.match(r"^p\.[A-Za-z]\d+[A-Za-z]$", na=False)] # regex pattern: p. - original aa - positon - new aa

print(df1[~df1[2].str.match(r"^p\.[A-Za-z]\d+[A-Za-z]$", na=False)]) # check the funny business


           0                    1                   2                    3
321   PTPN11         c.181_183del            p.D61del      Noonan syndrome
760   PTPN11     c.179_182delinsT    p.G60_D61delinsV      Noonan syndrome
940   PTPN11         c.179_181del            p.G60del      Noonan syndrome
1109  MAP2K2         c.186_197del        p.K63_E66del         CFC syndrome
1120  MAP2K2         c.186_197del        p.K63_E66del         CFC syndrome
1233  MAP2K1         c.175_177del            p.K59del    Costello syndrome
1484    SOS1       c.1435_1443dup      p.R479_P481dup         CFC syndrome
1527  MAP2K2         c.136_165del        p.L46_E55del         CFC syndrome
1544     CBL          c.1096-1G>C                 nan      Noonan syndrome
1545     CBL          c.1228-4A>G                 nan      Noonan syndrome
1695    BRAF       c.1384_1407del      p.R462_G469del         CFC syndrome
1702    BRAF       c.1408_1410del           p.T470del         CFC syndrome
1710  MAP2K1         c.17

In [11]:
NSEuronet_headers = ["Gene", "cDNA", "Protein", "Disease"] #headers to add to df
NSEuronet_df.columns = NSEuronet_headers

# Filter for gene
NSEuronet_gene_df = NSEuronet_df[NSEuronet_df["Gene"]==f'{gene}']

In [12]:
NSEuronet_gene_df

Gene                 cDNA  Protein              Disease
1     PTPN11             c.922A>G  p.N308D      Noonan syndrome
2     PTPN11             c.184T>G   p.Y62D      Noonan syndrome
3     PTPN11             c.922A>G  p.N308D      Noonan syndrome
4     PTPN11            c.1232C>T  p.T411M      Noonan syndrome
5     PTPN11            c.1232C>T  p.T411M      Noonan syndrome
6     PTPN11            c.1232C>T  p.T411M      Noonan syndrome
7     PTPN11            c.1529A>G  p.Q510R  NF1-Noonan syndrome
8     PTPN11             c.179G>C   p.G60A      Noonan syndrome
9     PTPN11             c.182A>G   p.D61G      Noonan syndrome
10    PTPN11             c.184T>G   p.Y62D      Noonan syndrome
11    PTPN11             c.188A>G   p.Y63C      Noonan syndrome
12    PTPN11             c.218C>T   p.T73I      Noonan syndrome
13    PTPN11             c.236A>G   p.Q79R      Noonan syndrome
14    PTPN11             c.236A>G   p.Q79R      Noonan syndrome
15    PTPN11             c.236A>G   p.Q79R      Noonan syndrome
16    PTPN11             c.317A>C  p.D106A      Noonan syndrome
17    PTPN11             c.417G>C  p.E139D      Noonan syndrome
18    PTPN11             c.417G>C  p.E139D      Noonan syndrome
19    PTPN11             c.854T>C  p.F285S      Noonan syndrome
20    PTPN11             c.923A>G  p.N308S      Noonan syndrome
21    PTPN11             c.923A>G  p.N308S      Noonan syndrome
22    PTPN11             c.923A>G  p.N308S      Noonan syndrome
23    PTPN11            c.1472C>A  p.P491H      Noonan syndrome
24    PTPN11            c.1471C>T  p.P491S      Noonan syndrome
25    PTPN11            c.1510A>G  p.M504V      Noonan syndrome
26    PTPN11            c.1505C>T  p.S502L      Noonan syndrome
27    PTPN11             c.836A>G  p.Y279C  LEOPARD syndrome...
28    PTPN11            c.1472C>T  p.P491L      Noonan syndrome
29    PTPN11            c.1472C>T  p.P491L      Noonan syndrome
30    PTPN11            c.1472C>T  p.P491L      Noonan syndrome
31    PTPN11             c.766C>A  p.Q256K      Noonan syndrome
32    PTPN11             c.923A>G  p.N308S      Noonan syndrome
33    PTPN11             c.218C>T   p.T73I      Noonan syndrome
34    PTPN11            c.1403C>T  p.T468M  LEOPARD syndrome...
35    PTPN11            c.1403C>T  p.T468M  LEOPARD syndrome...
36    PTPN11            c.1403C>T  p.T468M  LEOPARD syndrome...
37    PTPN11            c.1403C>T  p.T468M  LEOPARD syndrome...
38    PTPN11             c.218C>T   p.T73I      Noonan syndrome
39    PTPN11             c.172A>G   p.N58D      Noonan syndrome
40    PTPN11             c.188A>G   p.Y63C      Noonan syndrome
41    PTPN11             c.188A>G   p.Y63C      Noonan syndrome
42    PTPN11             c.188A>G   p.Y63C      Noonan syndrome
43    PTPN11             c.206A>T   p.E69V      Noonan syndrome
44    PTPN11             c.836A>G  p.Y279C      Noonan syndrome
45    PTPN11             c.844A>G  p.I282V      Noonan syndrome
46    PTPN11             c.922A>G  p.N308D      Noonan syndrome
47    PTPN11             c.922A>G  p.N308D      Noonan syndrome
48    PTPN11             c.922A>G  p.N308D      Noonan syndrome
49    PTPN11             c.922A>G  p.N308D      Noonan syndrome
50    PTPN11             c.922A>G  p.N308D      Noonan syndrome
51    PTPN11             c.922A>G  p.N308D      Noonan syndrome
52    PTPN11             c.922A>G  p.N308D      Noonan syndrome
53    PTPN11             c.922A>G  p.N308D      Noonan syndrome
54    PTPN11             c.922A>G  p.N308D      Noonan syndrome
55    PTPN11             c.922A>G  p.N308D      Noonan syndrome
56    PTPN11             c.922A>G  p.N308D      Noonan syndrome
57    PTPN11             c.923A>G  p.N308S      Noonan syndrome
58    PTPN11            c.1529A>C  p.Q510P      Noonan syndrome
59    PTPN11             c.922A>G  p.N308D      Noonan syndrome
60    PTPN11             c.182A>C   p.D61A      Noonan syndrome
61    PTPN11             c.214G>T   p.A72S      Noonan syndrome
62    PTPN11             c.236A>G   p.Q7

In [13]:
NSEuronet_gene_df.shape

(2193, 4)

#### ClinVar

NCBI E-utilities rate is limited to 3 requests per second (without an API key). Can request an NCBI API key to increase limit to ~10 per second.

Try again teXML release (gzipped) and parse for gene of interest

ClinVar maintains a complete set of variant data on an FTP server. Weekly update cycle but only the realease on the 1st Thursday of the month is archived. Download this below. https://pmc.ncbi.nlm.nih.gov/tools/ftp/

In [17]:
# Manually load the clinvar_result.txt download (for single gene e.g. PTPN11)

df2 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\clinvar_result.txt", sep="\t", low_memory=False)
print(df2.head())


                  Name              Gene(s) Protein change  \
0  GRCh38/hg38 12p1...  LOC130008261|LOC...            NaN   
1  GRCh38/hg38 12q2...  HECTD4|LOC130008...            NaN   
2  GRCh38/hg38 12q2...  HECTD4|LOC130008...            NaN   
3  GRCh38/hg38 12q2...          PTPN11|RPL6            NaN   
4  NM_002834.3(PTPN...          PTPN11|RPL6            NaN   

          Condition(s)     Accession  GRCh37Chromosome       GRCh37Location  \
0            See cases  VCV000150740              12.0   282465 - 133773393   
1            See cases  VCV000059818              12.0  112741234 - 1131...   
2            See cases  VCV000059819              12.0  112745336 - 1131...   
3            See cases  VCV000145960              12.0  112854667 - 1128...   
4  Noonan syndrome ...  VCV000882155              12.0            112856599   

   GRCh38Chromosome       GRCh38Location  VariationID  AlleleID(s)  \
0              12.0   121271 - 133196807       150740       160491   
1           

In [18]:
print(df2["Molecular consequence"].unique())


[nan '5 prime UTR variant' 'missense variant|initiator_codon_variant'
 'missense variant' 'synonymous variant' 'intron variant'
 'frameshift variant' 'splice acceptor variant|intron variant'
 'inframe_indel' 'inframe_deletion' 'inframe_insertion' 'nonsense'
 'splice donor variant' 'splice acceptor variant'
 'synonymous variant|intron variant' 'missense variant|intron variant'
 '3 prime UTR variant|intron variant' 'stop lost' '3 prime UTR variant']


In [13]:
# Filter for SNVs
df2_snvs = df2[~df2['GRCh38Location'].astype(str).str.contains('-')].copy() # Keep rows where GRCh38Location is a single number (i.e no hyphen)
df2_snvs = df2_snvs.dropna(subset=['GRCh38Location'])

# Convert GRCh38Location to int (for merging later)
df2_snvs['GRCh38Location'] = df2_snvs['GRCh38Location'].astype(int)


In [16]:
df2_snvs[df2_snvs["Protein change"].notna()]

Name Gene(s)       Protein change         Condition(s)  \
24    NM_002834.5(PTPN...  PTPN11                  M1R  Juvenile myelomo...   
25    NM_002834.5(PTPN...  PTPN11                  T2I  LEOPARD syndrome...   
30    NM_002834.5(PTPN...  PTPN11                  R4G         not provided   
31    NM_002834.5(PTPN...  PTPN11                  R4Q            RASopathy   
57    NM_002834.5(PTPN...  PTPN11                 W6fs            RASopathy   
58    NM_002834.5(PTPN...  PTPN11                  W6C  Cardiovascular p...   
59    NM_002834.5(PTPN...  PTPN11                  W6C  Cardiovascular p...   
60    NM_002834.5(PTPN...  PTPN11                 N10Y  not provided|Car...   
61    NM_002834.5(PTPN...  PTPN11                 N10H   Metachondromatosis   
62    NM_002834.5(PTPN...  PTPN11                 N10D  Cardiovascular p...   
63    NM_002834.5(PTPN...  PTPN11                 N10T  RASopathy|not pr...   
64    NM_002834.5(PTPN...  PTPN11                 N10S  not provided|RAS...   
65    NM_002834.5(PTPN...  PTPN11                 I11T            RASopathy   
66    NM_002834.5(PTPN...  PTPN11                 T12A            RASopathy   
69    NM_002834.5(PTPN...  PTPN11                 V14L         not provided   
72    NM_002834.5(PTPN...  PTPN11                 N18D  Cardiovascular p...   
73    NM_002834.5(PTPN...  PTPN11                 N18S            RASopathy   
75    NM_002834.5(PTPN...  PTPN11                 L19V            RASopathy   
77    NM_002834.5(PTPN...  PTPN11                 T22A  Juvenile myelomo...   
79    NM_002834.5(PTPN...  PTPN11                 G24A  Cardiovascular p...   
80    NM_002834.5(PTPN...  PTPN11                 G27D         not provided   
81    NM_002834.5(PTPN...  PTPN11                 A31S         not provided   
82    NM_002834.5(PTPN...  PTPN11                 A31G   LEOPARD syndrome 1   
86    NM_002834.5(PTPN...  PTPN11                 K35E            RASopathy   
87    NM_002834.5(PTPN...  PTPN11                 K35Q  Cardiovascular p...   
88    NM_002834.5(PTPN...  PTPN11                 K35I            RASopathy   
91    NM_002834.5(PTPN...  PTPN11                 G39R  RASopathy|not pr...   
93    NM_002834.5(PTPN...  PTPN11                 D40G        not specified   
95    NM_002834.5(PTPN...  PTPN11                 T42S         not provided   
96    NM_002834.5(PTPN...  PTPN11                 T42A  Noonan syndrome ...   
98    NM_002834.5(PTPN...  PTPN11                 L43V  RASopathy|LEOPAR...   
99    NM_002834.5(PTPN...  PTPN11                 L43F  RASopathy|Cardio...   
102   NM_002834.5(PTPN...  PTPN11                 V45I            RASopathy   
114   NM_002834.5(PTPN...  PTPN11           G48R, G49R  not provided|Ewi...   
115   NM_002834.5(PTPN...  PTPN11           A50T, A49T            RASopathy   
116   NM_002834.5(PTPN...  PTPN11           T51N, T52N            RASopathy   
117   NM_002834.5(PTPN...  PTPN11           T52I, T51I            RASopathy   
121   NM_002834.5(PTPN...  PTPN11           K55R, K54R            RASopathy   
122   NM_002834.5(PTPN...  PTPN11           I56V, I55V  Noonan syndrome ...   
123   NM_002834.5(PTPN...  PTPN11           I56T, I55T  Noonan syndrome ...   
126   NM_002834.5(PTPN...  PTPN11           Q56H, Q57H      Noonan syndrome   
129   NM_002834.5(PTPN...  PTPN11           N58Y, N57Y  not provided|RAS...   
130   NM_002834.5(PTPN...  PTPN11           N58D, N57D  Male infertility...   
131   NM_002834.5(PTPN...  PTPN11           N58H, N57H  not provided|RAS...   
132   NM_002834.5(PTPN...  PTPN11           N58S, N57S  Noonan syndrome ...   
133   NM_002834.5(PTPN...  PTPN11           N58K, N57K  Noonan syndrome|...   
134   NM_002834.5(PTPN...  PTPN11           N58K, N57K  Noonan syndrome ...   
135   NM_002834.5(PTPN...  PTPN11           T59A, T58A  not provided|PTP...   
137   NM_002834.5(PTPN...  PTPN11           G60R, G59R  not provided|RAS...   
138   NM_002834.5(PTPN...  PTPN11           G60C, G59C  Cardiovascular 

In [29]:
print(df2_snvs.columns.tolist())

['Name', 'Gene(s)', 'Protein change', 'Condition(s)', 'Accession', 'GRCh37Chromosome', 'GRCh37Location', 'GRCh38Chromosome', 'GRCh38Location', 'VariationID', 'AlleleID(s)', 'dbSNP ID', 'Canonical SPDI', 'Variant type', 'Molecular consequence', 'Germline classification', 'Germline date last evaluated', 'Germline review status', 'Somatic clinical impact', 'Somatic clinical impact date last evaluated', 'Somatic clinical impact review status', 'Oncogenicity classification', 'Oncogenicity date last evaluated', 'Oncogenicity review status', 'Unnamed: 24']


In [24]:
# Filter for missense variants
df2_missense = df2_snvs.assign(
    **{'Protein change': df2_snvs['Protein change'].str.split(',')}
).explode('Protein change')

df2_missense['Protein change'] = df2_missense['Protein change'].str.strip() # remove leading/trailing spaces

df2_missense = df2_missense[df2_missense['Protein change'].str.match(r"^[A-Za-z]\d+[A-Za-z]$", na=False)] # regex pattern: original aa - positon - new aa


In [25]:
# Extract ClinVar version of AA info
df2_missense['AAfrom'] = df2_missense['Protein change'].str[0]        # first character
df2_missense['AAto']   = df2_missense['Protein change'].str[-1]       # last character
df2_missense['AApos_ClinVar']  = df2_missense['Protein change'].str.extract(r'(\d+)').astype(int)  # numeric part


In [23]:
df2_missense

Name Gene(s) Protein change         Condition(s)  \
24    NM_002834.5(PTPN...  PTPN11            M1R  Juvenile myelomo...   
25    NM_002834.5(PTPN...  PTPN11            T2I  LEOPARD syndrome...   
30    NM_002834.5(PTPN...  PTPN11            R4G         not provided   
31    NM_002834.5(PTPN...  PTPN11            R4Q            RASopathy   
58    NM_002834.5(PTPN...  PTPN11            W6C  Cardiovascular p...   
59    NM_002834.5(PTPN...  PTPN11            W6C  Cardiovascular p...   
60    NM_002834.5(PTPN...  PTPN11           N10Y  not provided|Car...   
61    NM_002834.5(PTPN...  PTPN11           N10H   Metachondromatosis   
62    NM_002834.5(PTPN...  PTPN11           N10D  Cardiovascular p...   
63    NM_002834.5(PTPN...  PTPN11           N10T  RASopathy|not pr...   
64    NM_002834.5(PTPN...  PTPN11           N10S  not provided|RAS...   
65    NM_002834.5(PTPN...  PTPN11           I11T            RASopathy   
66    NM_002834.5(PTPN...  PTPN11           T12A            RASopathy   
69    NM_002834.5(PTPN...  PTPN11           V14L         not provided   
72    NM_002834.5(PTPN...  PTPN11           N18D  Cardiovascular p...   
73    NM_002834.5(PTPN...  PTPN11           N18S            RASopathy   
75    NM_002834.5(PTPN...  PTPN11           L19V            RASopathy   
77    NM_002834.5(PTPN...  PTPN11           T22A  Juvenile myelomo...   
79    NM_002834.5(PTPN...  PTPN11           G24A  Cardiovascular p...   
80    NM_002834.5(PTPN...  PTPN11           G27D         not provided   
81    NM_002834.5(PTPN...  PTPN11           A31S         not provided   
82    NM_002834.5(PTPN...  PTPN11           A31G   LEOPARD syndrome 1   
86    NM_002834.5(PTPN...  PTPN11           K35E            RASopathy   
87    NM_002834.5(PTPN...  PTPN11           K35Q  Cardiovascular p...   
88    NM_002834.5(PTPN...  PTPN11           K35I            RASopathy   
91    NM_002834.5(PTPN...  PTPN11           G39R  RASopathy|not pr...   
93    NM_002834.5(PTPN...  PTPN11           D40G        not specified   
95    NM_002834.5(PTPN...  PTPN11           T42S         not provided   
96    NM_002834.5(PTPN...  PTPN11           T42A  Noonan syndrome ...   
98    NM_002834.5(PTPN...  PTPN11           L43V  RASopathy|LEOPAR...   
99    NM_002834.5(PTPN...  PTPN11           L43F  RASopathy|Cardio...   
102   NM_002834.5(PTPN...  PTPN11           V45I            RASopathy   
114   NM_002834.5(PTPN...  PTPN11           G48R  not provided|Ewi...   
114   NM_002834.5(PTPN...  PTPN11           G49R  not provided|Ewi...   
115   NM_002834.5(PTPN...  PTPN11           A50T            RASopathy   
115   NM_002834.5(PTPN...  PTPN11           A49T            RASopathy   
116   NM_002834.5(PTPN...  PTPN11           T51N            RASopathy   
116   NM_002834.5(PTPN...  PTPN11           T52N            RASopathy   
117   NM_002834.5(PTPN...  PTPN11           T52I            RASopathy   
117   NM_002834.5(PTPN...  PTPN11           T51I            RASopathy   
121   NM_002834.5(PTPN...  PTPN11           K55R            RASopathy   
121   NM_002834.5(PTPN...  PTPN11           K54R            RASopathy   
122   NM_002834.5(PTPN...  PTPN11           I56V  Noonan syndrome ...   
122   NM_002834.5(PTPN...  PTPN11           I55V  Noonan syndrome ...   
123   NM_002834.5(PTPN...  PTPN11           I56T  Noonan syndrome ...   
123   NM_002834.5(PTPN...  PTPN11           I55T  Noonan syndrome ...   
126   NM_002834.5(PTPN...  PTPN11           Q56H      Noonan syndrome   
126   NM_002834.5(PTPN...  PTPN11           Q57H      Noonan syndrome   
129   NM_002834.5(PTPN...  PTPN11           N58Y  not provided|RAS...   
129   NM_002834.5(PTPN...  PTPN11           N57Y  not provided|RAS...   
130   NM_002834.5(PTPN...  PTPN11           N58D  Male infertility...   
130   NM_002834.5(PTPN...  PTPN11           N57D  Male infertility...   
131   NM_002834.5(PTPN...  PTPN11           N58H  not provided|RAS...   
131   NM_002834.5(PTPN...  PTPN11           N57H  not provided|RAS...   
132   

###### Parse Uniprot reference sequence

In [21]:
# Dictionary of Uniprot IDs for each gene
uniprot_ids = {
    "PTPN11": "Q06124",    
}

# Function to return Uniprot reference sequence as a string
def get_uniprot_sequence(gene):
    uniprot_id = uniprot_ids[gene]
    url = f"https://www.uniprot.org/uniprot/{uniprot_id}.fasta"
    
    response = requests.get(url)
    
    seq_record = SeqIO.read(StringIO(response.text), "fasta")
    sequence = str(seq_record.seq)
    
    return sequence

uniprot_sequence = get_uniprot_sequence(gene)


In [27]:
# Compare ClinVar amino acids to Uniprot sequence
df2_missense['matches_Uniprot'] = df2_missense.apply(
    lambda row: (
        isinstance(row['AApos_ClinVar'], (int, float)) and
        1 <= row['AApos_ClinVar'] <= len(uniprot_sequence) and
        uniprot_sequence[int(row['AApos_ClinVar']) - 1] == row['AAfrom']
    ),
    axis=1
)

# Filter ClinVar AA info that matches Uniprot reference 
df2_missense = df2_missense[df2_missense['matches_Uniprot']]

#### REVEL

Downloaded from https://sites.google.com/site/revelgenomics/downloads

Try again to curl from dfNSFP

In [24]:
# Manually download the REVEL data (for all genes)

# Read just the first 10 rows (6GB REVEL file)
df3 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\revel-v1.3_all_chromosomes\revel_with_transcript_ids", nrows=10)
df3

chr  hg19_pos  grch38_pos ref alt aaref aaalt  REVEL Ensembl_transcriptid
0    1     35142       35142   G   A     T     M  0.027      ENST00000417324
1    1     35142       35142   G   C     T     R  0.035      ENST00000417324
2    1     35142       35142   G   T     T     K  0.043      ENST00000417324
3    1     35143       35143   T   A     T     S  0.018      ENST00000417324
4    1     35143       35143   T   C     T     A  0.034      ENST00000417324
5    1     35143       35143   T   G     T     P  0.039      ENST00000417324
6    1     35144       35144   A   C     C     W  0.012      ENST00000417324
7    1     35145       35145   C   A     C     F  0.023      ENST00000417324
8    1     35145       35145   C   G     C     S  0.029      ENST00000417324
9    1     35145       35145   C   T     C     Y  0.016      ENST00000417324

In [78]:
min_pos = min(df2_snvs['GRCh38Location'])
max_pos = max(df2_snvs['GRCh38Location'])
chrom = df2_snvs['GRCh38Chromosome'].unique()[0]


In [79]:
revel_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\revel-v1.3_all_chromosomes\revel_with_transcript_ids"
PTPN11_revel_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv" #output file

chunksize = 1_000_000
ptpn11_revel_chunks = []

for chunk in pd.read_csv(revel_file, chunksize=chunksize, low_memory=False):
    # Convert positions in revel_file to numeric
    chunk['grch38_pos'] = pd.to_numeric(chunk['grch38_pos'], errors='coerce')
    
    # Only keep PTPN11 chromosome
    chunk = chunk[chunk['chr'] == chrom]
    
    # Keep only positions within PTPN11 range
    filtered_chunk = chunk[
        (chunk['grch38_pos'] >= min_pos) &
        (chunk['grch38_pos'] <= max_pos)
    ]
    
    if not filtered_chunk.empty:
        ptpn11_revel_chunks.append(filtered_chunk)
    
    # Early stop: REVEL is sorted by grch38_pos
    if chunk['grch38_pos'].max() > max_pos:
        break

# Concatenate all filtered chunks
if ptpn11_revel_chunks:
    ptpn11_revel = pd.concat(ptpn11_revel_chunks)
    ptpn11_revel.to_csv(PTPN11_revel_file, index=False)
    print(f"Filtered REVEL for PTPN11 saved to:\n{PTPN11_revel_file}")

ParserError: Error tokenizing data. C error: Calling read(nbytes) on source failed. Try engine='python'.

In [7]:
ptpn11_revel = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv") #output file


In [8]:
ptpn11_revel

chr   hg19_pos   grch38_pos ref alt aaref aaalt  REVEL  \
0      12  112856916  112419112.0   A   C     M     L  0.263   
1      12  112856916  112419112.0   A   G     M     V  0.301   
2      12  112856916  112419112.0   A   T     M     L  0.263   
3      12  112856917  112419113.0   T   A     M     K  0.294   
4      12  112856917  112419113.0   T   C     M     T  0.315   
5      12  112856917  112419113.0   T   G     M     R  0.202   
6      12  112856918  112419114.0   G   A     M     I  0.222   
7      12  112856918  112419114.0   G   C     M     I  0.222   
8      12  112856918  112419114.0   G   T     M     I  0.222   
9      12  112856919  112419115.0   A   C     T     P  0.194   
10     12  112856919  112419115.0   A   G     T     A  0.054   
11     12  112856919  112419115.0   A   T     T     S  0.048   
12     12  112856920  112419116.0   C   A     T     K  0.155   
13     12  112856920  112419116.0   C   G     T     R  0.063   
14     12  112856920  112419116.0   C   T     T     I  0.213   
15     12  112856922  112419118.0   T   A     S     T  0.363   
16     12  112856922  112419118.0   T   C     S     P  0.647   
17     12  112856922  112419118.0   T   G     S     A  0.303   
18     12  112856923  112419119.0   C   G     S     W  0.710   
19     12  112856923  112419119.0   C   T     S     L  0.630   
20     12  112856925  112419121.0   C   G     R     G  0.518   
21     12  112856925  112419121.0   C   T     R     W  0.771   
22     12  112856926  112419122.0   G   A     R     Q  0.393   
23     12  112856926  112419122.0   G   C     R     P  0.635   
24     12  112856926  112419122.0   G   T     R     L  0.432   
25     12  112856928  112419124.0   A   G     R     G  0.565   
26     12  112856929  112419125.0   G   A     R     K  0.394   
27     12  112856929  112419125.0   G   C     R     T  0.774   
28     12  112856929  112419125.0   G   T     R     I  0.819   
29     12  112884080  112446276.0   A   C     R     S  0.721   
30     12  112884080  112446276.0   A   T     R     S  0.716   
31     12  112884081  112446277.0   T   A     W     R  0.941   
32     12  112884081  112446277.0   T   C     W     R  0.941   
33     12  112884081  112446277.0   T   G     W     G  0.957   
34     12  112884082  112446278.0   G   C     W     S  0.916   
35     12  112884082  112446278.0   G   T     W     L  0.897   
36     12  112884083  112446279.0   G   C     W     C  0.920   
37     12  112884083  112446279.0   G   T     W     C  0.920   
38     12  112884084  112446280.0   T   A     F     I  0.965   
39     12  112884084  112446280.0   T   C     F     L  0.945   
40     12  112884084  112446280.0   T   G     F     V  0.970   
41     12  112884085  112446281.0   T   A     F     Y  0.834   
42     12  112884085  112446281.0   T   C     F     S  0.980   
43     12  112884085  112446281.0   T   G     F     C  0.976   
44     12  112884086  112446282.0   T   A     F     L  0.888   
45     12  112884086  112446282.0   T   G     F     L  0.888   
46     12  112884087  112446283.0   C   A     H     N  0.864   
47     12  112884087  112446283.0   C   G     H     D  0.932   
48     12  112884087  112446283.0   C   T     H     Y  0.801   
49     12  112884088  112446284.0   A   C     H     P  0.969   
50     12  112884088  112446284.0   A   G     H     R  0.965   
51     12  112884088  112446284.0   A   T     H     L  0.928   
52     12  112884089  112446285.0   C   A     H     Q  0.916   
53     12  112884089  112446285.0   C   G     H     Q  0.916   
54     12  112884090  112446286.0   C   A     P     T  0.655   
55     12  112884090  112446286.0   C   G     P     A  0.540   
56     12  112884090  112446286.0   C   T     P     S  0.662   
57     12  112884091  112446287.0   C   A     P     Q  0.680   
58     12  112884091  112446287.0   C   G     P     R  0.591   
59     12  112884091  112446287.0   C   T     P     L  0.754   
60     12  112884093  112446289.0   A   C     N     H  0.436   
61     12  112884093  112446289.0   A 

In [63]:
ptpn11_revel.shape

(4645, 9)

#### BayesDel

Downloaded from https://drive.google.com/drive/folders/1K4LI6ZSsUGBhHoChUtegC8bgCt7hbQlA (2017! version)

Need to install and run VICTOR locally (Linux)


In [98]:
min_pos_37 = int(min(df2_snvs['GRCh37Location']))
max_pos_37 = int(max(df2_snvs['GRCh37Location']))
chrom_37 = int(df2_snvs['GRCh37Chromosome'].unique()[0])

In [75]:
# Unzipped file path for gene specific chrom and GRCH37 location
bayesdel_noAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"

with open(bayesdel_noAF_file, "r") as f:
    for _ in range(10):
        print(f.readline().strip())


#Chr	Start	ref	alt	BayesDel_nsfp33a_noAF
12	176049	A	C	-0.217265
12	176049	A	G	-0.171535
12	176049	A	T	-0.21727
12	176050	T	A	-0.288296
12	176050	T	C	-0.265607
12	176050	T	G	-0.301534
12	176051	G	A	-0.0488746
12	176051	G	C	-0.0488725
12	176051	G	T	-0.048873


In [101]:
def load_bayesdel_region(file_path, min_pos, max_pos, output_csv=None, chunksize=100_000, columns=None):
    chunks = []
    if columns is None:
        columns = ["Chr", "Start", "Ref", "Alt", "Score"]

    for chunk in pd.read_csv(file_path, sep="\t", names=columns, chunksize=chunksize, comment="#"):
        chunk["Start"] = pd.to_numeric(chunk["Start"], errors="coerce")
        # Filter by genomic position
        filtered = chunk[(chunk["Start"] >= min_pos) & (chunk["Start"] <= max_pos)]

        if not filtered.empty:
            chunks.append(filtered)

    if chunks:
        df_region = pd.concat(chunks, ignore_index=True)

    # Save to CSV 
    if output_csv:
        df_region.to_csv(output_csv, index=False)
        
    return df_region





In [110]:
bayesdel_noAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"
bayesdel_addAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"


# Load noAF region
PTPN11_bayesdel_noAF = load_bayesdel_region(bayesdel_noAF_file, min_pos_37, max_pos_37, output_csv=r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_noAF.csv")

# Load addAF region
PTPN11_bayesdel_addAF = load_bayesdel_region(bayesdel_addAF_file, min_pos_37, max_pos_37, output_csv=r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_addAF.csv")

#print("\nnoAF columns:", df_noAF.columns.tolist())
#print("\naddAF columns:", df_addAF.columns.tolist())

In [113]:
PTPN11_bayesdel_noAF


Chr      Start Ref Alt     Score
0      12  112856916   A   C -0.026848
1      12  112856916   A   G  0.002997
2      12  112856916   A   T -0.026849
3      12  112856917   T   A  0.660000
4      12  112856917   T   C  0.660000
5      12  112856917   T   G  0.660000
6      12  112856918   G   A  0.660000
7      12  112856918   G   C  0.660000
8      12  112856918   G   T  0.660000
9      12  112856919   A   C -0.124339
10     12  112856919   A   G -0.279529
11     12  112856919   A   T -0.328977
12     12  112856920   C   A -0.079163
13     12  112856920   C   G -0.222939
14     12  112856920   C   T  0.010807
15     12  112856922   T   A -0.047711
16     12  112856922   T   C  0.078514
17     12  112856922   T   G -0.133369
18     12  112856923   C   A  0.660000
19     12  112856923   C   G  0.135564
20     12  112856923   C   T  0.074035
21     12  112856925   C   G  0.044882
22     12  112856925   C   T  0.095303
23     12  112856926   G   A -0.022043
24     12  112856926   G   C  0.020690
25     12  112856926   G   T  0.039940
26     12  112856928   A   G  0.010889
27     12  112856928   A   T  0.660000
28     12  112856929   G   A -0.041776
29     12  112856929   G   C  0.000317
30     12  112856929   G   T  0.102413
31     12  112856930   G   A  0.660000
32     12  112856930   G   C  0.660000
33     12  112856930   G   T  0.660000
34     12  112856931   T   A  0.660000
35     12  112856931   T   C  0.660000
36     12  112856931   T   G  0.660000
37     12  112884078   A   C  0.660000
38     12  112884078   A   G  0.660000
39     12  112884078   A   T  0.660000
40     12  112884079   G   A  0.660000
41     12  112884079   G   C  0.660000
42     12  112884079   G   T  0.660000
43     12  112884080   A   C  0.046103
44     12  112884080   A   T  0.046094
45     12  112884081   T   A  0.548487
46     12  112884081   T   C  0.548482
47     12  112884081   T   G  0.539868
48     12  112884082   G   A  0.660000
49     12  112884082   G   C  0.556368
50     12  112884082   G   T  0.550287
51     12  112884083   G   A  0.660000
52     12  112884083   G   C  0.512606
53     12  112884083   G   T  0.512606
54     12  112884084   T   A  0.559639
55     12  112884084   T   C  0.509503
56     12  112884084   T   G  0.604626
57     12  112884085   T   A  0.210138
58     12  112884085   T   C  0.612920
59     12  112884085   T   G  0.612914
60     12  112884086   T   A  0.456428
61     12  112884086   T   G  0.456431
62     12  112884087   C   A  0.264645
63     12  112884087   C   G  0.579112
64     12  112884087   C   T  0.254462
65     12  112884088   A   C  0.585375
66     12  112884088   A   G  0.474986
67     12  112884088   A   T  0.352207
68     12  112884089   C   A  0.361009
69     12  112884089   C   G  0.361013
70     12  112884090   C   A  0.225964
71     12  112884090   C   G  0.129085
72     12  112884090   C   T  0.180856
73     12  112884091   C   A  0.216050
74     12  112884091   C   G  0.392990
75     12  112884091   C   T  0.283123
76     12  112884093   A   C -0.077980
77     12  112884093   A   G -0.184288
78     12  112884093   A   T  0.156500
79     12  112884094   A   C -0.082037
80     12  112884094   A   G -0.234164
81     12  112884094   A   T  0.200155
82     12  112884095   T   A -0.171981
83     12  112884095   T   G -0.171978
84     12  112884096   A   C  0.043692
85     12  112884096   A   G -0.006434
86     12  112884096   A   T  0.263725
87     12  112884097   T   A  0.351845
88     12  112884097   T   C  0.406204
89     12  112884097   T   G  0.466207
90     12  112884098   C   G  0.099829
91     12  112884099   A   C  0.223980
92     12  112884099   A   G  0.082451
93     12  112884099   A   T -0.119820
94     12  112884100   C   A -0.022180
95     12  112884100   C   G -0.158125
96     12  112884100   C   T  0.081891
97     12  112884102   G   A  0.221889
98     12  112884102   G   C  0.313496
99     12  112884102   G   T  0.452639
100    12  112884103   G   A  0.432610
101    12  112884103   G   C

##### Merge Revel & BayesDel

In [122]:
# Load PTPN11_REVEL and BayesDel
revel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv")
PTPN11_bayesdel_noAF_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_noAF.csv")
PTPN11_bayesdel_addAF_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_addAF.csv")


# Take aggregate REVEL for multiple SNVs
#revel_df_agg = revel_df.groupby(['grch38_pos','aaref','aaalt'], as_index=False)['REVEL'].mean()

# Merge PTPN11_REVEL mean scores on ClinVar
PTPN11_bayesdel_noAF_df = PTPN11_bayesdel_noAF_df.rename(columns={"Score": "BayesDel_noAF"})
PTPN11_bayesdel_addAF_df = PTPN11_bayesdel_addAF_df.rename(columns={"Score": "BayesDel_addAF"})


revel_bayesdel_noAF_df = pd.merge(
    revel_df,
    PTPN11_bayesdel_noAF_df,
    left_on=['hg19_pos', 'ref', 'alt'],
    right_on=['Start', 'Ref', 'Alt'],
    how='left',
)

revel_bayesdel_noAF_df = revel_bayesdel_noAF_df.drop(columns=['Chr','Start', 'Ref', 'Alt'])


revel_bayesdel_df = pd.merge(
    revel_bayesdel_noAF_df,
    PTPN11_bayesdel_addAF_df,
    left_on=['hg19_pos', 'ref', 'alt'],
    right_on=['Start', 'Ref', 'Alt'],
    how='left',
)

revel_bayesdel_df = revel_bayesdel_df.drop(columns=['Chr','Start', 'Ref', 'Alt'])


In [123]:
print(revel_bayesdel_df.head())

   chr   hg19_pos   grch38_pos ref alt aaref aaalt  REVEL  \
0   12  112856916  112419112.0   A   C     M     L  0.263   
1   12  112856916  112419112.0   A   G     M     V  0.301   
2   12  112856916  112419112.0   A   T     M     L  0.263   
3   12  112856917  112419113.0   T   A     M     K  0.294   
4   12  112856917  112419113.0   T   C     M     T  0.315   

  Ensembl_transcriptid  BayesDel_noAF  BayesDel_addAF  
0  ENST00000392597;...      -0.026848       -0.026848  
1  ENST00000392597;...       0.002997        0.002997  
2  ENST00000392597;...      -0.026849       -0.026849  
3  ENST00000392597;...       0.660000        0.660000  
4  ENST00000392597;...       0.660000        0.660000  


In [124]:
revel_bayesdel_df.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv", index=False)


### Uniprot

In [73]:
# Fetch domains and sites from UniProt

def get_uniprot_features(gene):
    uniprot_id = uniprot_ids[gene]
    url = f"https://rest.uniprot.org/uniprotkb/{uniprot_id}.json"
    response = requests.get(url)
    response.raise_for_status()
    data = response.json()
    
    domains_list = []
    sites_list = []
    
    # Assign colors for each feature type
    feature_colours = {
        'Domain': "#66c2a5",
        'Region': "#fc8d62",
        'Active site': "#e78ac3",
        'Binding site': "#a6d854"
    }
    
    for feature in data.get('features', []):
        ftype = feature['type']
        start = feature['location']['start']['value']
        end = feature['location']['end']['value']
        name = feature.get('description', ftype)
        
        # Collect domains
        if ftype in ['Domain', 'Region']:
            domains_list.append([name, start, end, feature_colours[ftype]])
        # Collect sites
        elif ftype in ['Active site', 'Binding site']:
            sites_list.append([name, start, end, feature_colours[ftype]])
    
    # Assign distinct colors for domains
    palette = sns.color_palette("Set2", n_colors=len(domains_list))
    for i, domain in enumerate(domains_list):
        domain[3] = palette[i]
    
    return domains_list, sites_list

In [74]:
domains, sites = get_uniprot_features(gene)

print("Domains / regions:")
for domain in domains:
    print (domain)

print("\nActive / binding sites:")
for site in sites:
    print (site)

# Save features dictionaries
all_features = {
    "domains": domains,
    "sites": sites
}

with open(f"{gene}_features.json", "w") as f:
    json.dump(all_features, f, indent=2)

Domains / regions:
['SH2 1', 6, 102, (0.4, 0.7607843137254902, 0.6470588235294118)]
['SH2 2', 112, 216, (0.9882352941176471, 0.5529411764705883, 0.3843137254901961)]
['Tyrosine-protein phosphatase', 247, 517, (0.5529411764705883, 0.6274509803921569, 0.796078431372549)]
['Disordered', 548, 571, (0.9058823529411765, 0.5411764705882353, 0.7647058823529411)]

Active / binding sites:
['Phosphocysteine intermediate', 459, 459, '#e78ac3']
['', 425, 425, '#a6d854']
['', 459, 465, '#a6d854']
['', 506, 506, '#a6d854']


In [43]:
uniprot_id = "Q06124"  # PTPN11
url = f"https://rest.uniprot.org/uniprotkb/{uniprot_id}.json"
response = requests.get(url)
response.raise_for_status()

data = response.json()  # <-- now data exists
print(data.keys())      # check top-level keys
print(json.dumps(data, indent=2)[:500])  # print fir

dict_keys(['entryType', 'primaryAccession', 'secondaryAccessions', 'uniProtkbId', 'entryAudit', 'annotationScore', 'organism', 'proteinExistence', 'proteinDescription', 'genes', 'comments', 'features', 'keywords', 'references', 'uniProtKBCrossReferences', 'sequence', 'extraAttributes'])
{
  "entryType": "UniProtKB reviewed (Swiss-Prot)",
  "primaryAccession": "Q06124",
  "secondaryAccessions": [
    "A8K1D9",
    "Q96HD7"
  ],
  "uniProtkbId": "PTN11_HUMAN",
  "entryAudit": {
    "firstPublicDate": "1994-02-01",
    "lastAnnotationUpdateDate": "2025-06-18",
    "lastSequenceUpdateDate": "2019-12-11",
    "entryVersion": 267,
    "sequenceVersion": 3
  },
  "annotationScore": 5.0,
  "organism": {
    "scientificName": "Homo sapiens",
    "commonName": "Human",
    "taxonId": 960


In [44]:
features = data.get('features')
print(features)  
print(len(features))
if features:
    print([f['type'] for f in features[:10]])


[{'type': 'Initiator methionine', 'location': {'start': {'value': 1, 'modifier': 'EXACT'}, 'end': {'value': 1, 'modifier': 'EXACT'}}, 'description': 'Removed', 'evidences': [{'evidenceCode': 'ECO:0007744', 'source': 'PubMed', 'id': '19413330'}]}, {'type': 'Chain', 'location': {'start': {'value': 2, 'modifier': 'EXACT'}, 'end': {'value': 593, 'modifier': 'EXACT'}}, 'description': 'Tyrosine-protein phosphatase non-receptor type 11', 'featureId': 'PRO_0000094767'}, {'type': 'Domain', 'location': {'start': {'value': 6, 'modifier': 'EXACT'}, 'end': {'value': 102, 'modifier': 'EXACT'}}, 'description': 'SH2 1', 'evidences': [{'evidenceCode': 'ECO:0000255', 'source': 'PROSITE-ProRule', 'id': 'PRU00191'}]}, {'type': 'Domain', 'location': {'start': {'value': 112, 'modifier': 'EXACT'}, 'end': {'value': 216, 'modifier': 'EXACT'}}, 'description': 'SH2 2', 'evidences': [{'evidenceCode': 'ECO:0000255', 'source': 'PROSITE-ProRule', 'id': 'PRU00191'}]}, {'type': 'Domain', 'location': {'start': {'value'

### Create datasets

#### Meta-predictor analysis

In [128]:
revel_bayesdel_df[revel_bayesdel_df.duplicated(subset=['grch38_pos','aaref','aaalt'], keep=False)]

chr   hg19_pos   grch38_pos ref alt aaref aaalt  REVEL  \
0      12  112856916  112419112.0   A   C     M     L  0.263   
2      12  112856916  112419112.0   A   T     M     L  0.263   
6      12  112856918  112419114.0   G   A     M     I  0.222   
7      12  112856918  112419114.0   G   C     M     I  0.222   
8      12  112856918  112419114.0   G   T     M     I  0.222   
29     12  112884080  112446276.0   A   C     R     S  0.721   
30     12  112884080  112446276.0   A   T     R     S  0.716   
31     12  112884081  112446277.0   T   A     W     R  0.941   
32     12  112884081  112446277.0   T   C     W     R  0.941   
36     12  112884083  112446279.0   G   C     W     C  0.920   
37     12  112884083  112446279.0   G   T     W     C  0.920   
44     12  112884086  112446282.0   T   A     F     L  0.888   
45     12  112884086  112446282.0   T   G     F     L  0.888   
52     12  112884089  112446285.0   C   A     H     Q  0.916   
53     12  112884089  112446285.0   C   G     H     Q  0.916   
66     12  112884095  112446291.0   T   A     N     K  0.454   
67     12  112884095  112446291.0   T   G     N     K  0.454   
88     12  112884105  112446301.0   G   C     V     L  0.375   
89     12  112884105  112446301.0   G   T     V     L  0.375   
98     12  112884110  112446306.0   G   C     E     D  0.354   
99     12  112884110  112446306.0   G   T     E     D  0.354   
111    12  112884116  112446312.0   A   C     E     D  0.827   
112    12  112884116  112446312.0   A   T     E     D  0.827   
119    12  112884119  112446315.0   C   A     N     K  0.331   
120    12  112884119  112446315.0   C   G     N     K  0.331   
135    12  112884128  112446324.0   G   C     L     F  0.597   
136    12  112884128  112446324.0   G   T     L     F  0.597   
147    12  112884134  112446330.0   A   C     R     S  0.600   
148    12  112884134  112446330.0   A   T     R     S  0.599   
149    12  112884135  112446331.0   G   A     G     R  0.873   
150    12  112884135  112446331.0   G   C     G     R  0.873   
166    12  112884143  112446339.0   T   A     D     E  0.316   
167    12  112884143  112446339.0   T   G     D     E  0.316   
180    12  112884149  112446345.0   T   A     S     R  0.907   
181    12  112884149  112446345.0   T   G     S     R  0.907   
188    12  112884152  112446348.0   T   A     F     L  0.901   
189    12  112884152  112446348.0   T   G     F     L  0.901   
194    12  112884155  112446351.0   G   C     L     F  0.909   
195    12  112884155  112446351.0   G   T     L     F  0.909   
207    12  112884161  112446357.0   G   C     R     S  0.878   
208    12  112884161  112446357.0   G   T     R     S  0.878   
221    12  112884167  112446363.0   T   A     S     R  0.843   
222    12  112884167  112446363.0   T   G     S     R  0.843   
228    12  112884170  112446366.0   A   C     K     N  0.454   
229    12  112884170  112446366.0   A   T     K     N  0.454   
236    12  112884173  112446369.0   T   A     S     R  0.669   
237    12  112884173  112446369.0   T   G     S     R  0.671   
244    12  112884176  112446372.0   C   A     N     K  0.352   
245    12  112884176  112446372.0   C   G     N     K  0.352   
252    12  112884180  112446376.0   G   A     G     R  0.920   
253    12  112884180  112446376.0   G   C     G     R  0.919   
263    12  112884185  112446381.0   C   A     D     E  0.596   
264    12  112884185  112446381.0   C   G     D     E  0.596   
271    12  112884188  112446384.0   C   A     F     L  0.867   
272    12  112884188  112446384.0   C   G     F     L  0.867   
301    12  112888122  112450318.0   A   C     R     S  0.822   
302    12  112888122  112450318.0   A   T     R     S  0.838   
307    12  112888125  112450321.0   A   C     R     S  0.742   
308    12  112888125  112450321.0   A   T     R     S  0.742   
315    12  112888128  112450324.0   T   A     N     K  0.473   
316    12  112888128  112450324.0   T   G     N     K  0.473   
317    12  112888129  112450325.0   G 

In [138]:
# Load PTPN11_REVEL_BayesDel
revel_bayesdel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv")

# Take aggregate REVEL and BayesDel for multiple SNVs
revel_bayesdel_df_agg = revel_bayesdel_df.groupby(['grch38_pos','aaref','aaalt'], as_index=False)[['REVEL','BayesDel_noAF','BayesDel_addAF']].mean()

# Merge mean scores on ClinVar
df_stat = pd.merge(
    df2_missense,
    revel_bayesdel_df_agg,
    left_on=['GRCh38Location', 'AAfrom', 'AAto'],
    right_on=['grch38_pos', 'aaref', 'aaalt'],
    how='left'  # keep all ClinVar missense
)


In [37]:
df2_missense.shape

(588, 29)

In [134]:
df_stat

Name Gene(s) Protein change         Condition(s)  \
0    NM_002834.5(PTPN...  PTPN11            M1R  Juvenile myelomo...   
1    NM_002834.5(PTPN...  PTPN11            T2I  LEOPARD syndrome...   
2    NM_002834.5(PTPN...  PTPN11            R4G         not provided   
3    NM_002834.5(PTPN...  PTPN11            R4Q            RASopathy   
4    NM_002834.5(PTPN...  PTPN11            W6C  Cardiovascular p...   
5    NM_002834.5(PTPN...  PTPN11            W6C  Cardiovascular p...   
6    NM_002834.5(PTPN...  PTPN11           N10Y  not provided|Car...   
7    NM_002834.5(PTPN...  PTPN11           N10H   Metachondromatosis   
8    NM_002834.5(PTPN...  PTPN11           N10D  Cardiovascular p...   
9    NM_002834.5(PTPN...  PTPN11           N10T  RASopathy|not pr...   
10   NM_002834.5(PTPN...  PTPN11           N10S  not provided|RAS...   
11   NM_002834.5(PTPN...  PTPN11           I11T            RASopathy   
12   NM_002834.5(PTPN...  PTPN11           T12A            RASopathy   
13   NM_002834.5(PTPN...  PTPN11           V14L         not provided   
14   NM_002834.5(PTPN...  PTPN11           N18D  Cardiovascular p...   
15   NM_002834.5(PTPN...  PTPN11           N18S            RASopathy   
16   NM_002834.5(PTPN...  PTPN11           L19V            RASopathy   
17   NM_002834.5(PTPN...  PTPN11           T22A  Juvenile myelomo...   
18   NM_002834.5(PTPN...  PTPN11           G24A  Cardiovascular p...   
19   NM_002834.5(PTPN...  PTPN11           G27D         not provided   
20   NM_002834.5(PTPN...  PTPN11           A31S         not provided   
21   NM_002834.5(PTPN...  PTPN11           A31G   LEOPARD syndrome 1   
22   NM_002834.5(PTPN...  PTPN11           K35E            RASopathy   
23   NM_002834.5(PTPN...  PTPN11           K35Q  Cardiovascular p...   
24   NM_002834.5(PTPN...  PTPN11           K35I            RASopathy   
25   NM_002834.5(PTPN...  PTPN11           G39R  RASopathy|not pr...   
26   NM_002834.5(PTPN...  PTPN11           D40G        not specified   
27   NM_002834.5(PTPN...  PTPN11           T42S         not provided   
28   NM_002834.5(PTPN...  PTPN11           T42A  Noonan syndrome ...   
29   NM_002834.5(PTPN...  PTPN11           L43V  RASopathy|LEOPAR...   
30   NM_002834.5(PTPN...  PTPN11           L43F  RASopathy|Cardio...   
31   NM_002834.5(PTPN...  PTPN11           V45I            RASopathy   
32   NM_002834.5(PTPN...  PTPN11           G49R  not provided|Ewi...   
33   NM_002834.5(PTPN...  PTPN11           A50T            RASopathy   
34   NM_002834.5(PTPN...  PTPN11           T52N            RASopathy   
35   NM_002834.5(PTPN...  PTPN11           T52I            RASopathy   
36   NM_002834.5(PTPN...  PTPN11           K55R            RASopathy   
37   NM_002834.5(PTPN...  PTPN11           I56V  Noonan syndrome ...   
38   NM_002834.5(PTPN...  PTPN11           I56T  Noonan syndrome ...   
39   NM_002834.5(PTPN...  PTPN11           Q57H      Noonan syndrome   
40   NM_002834.5(PTPN...  PTPN11           N58Y  not provided|RAS...   
41   NM_002834.5(PTPN...  PTPN11           N58D  Male infertility...   
42   NM_002834.5(PTPN...  PTPN11           N58H  not provided|RAS...   
43   NM_002834.5(PTPN...  PTPN11           N58S  Noonan syndrome ...   
44   NM_002834.5(PTPN...  PTPN11           N58K  Noonan syndrome|...   
45   NM_002834.5(PTPN...  PTPN11           N58K  Noonan syndrome ...   
46   NM_002834.5(PTPN...  PTPN11           T59A  not provided|PTP...   
47   NM_002834.5(PTPN...  PTPN11           G60R  not provided|RAS...   
48   NM_002834.5(PTPN...  PTPN11           G60C  Cardiovascular p...   
49   NM_002834.5(PTPN...  PTPN11           G60S  PTPN11-related d...   
50   NM_002834.5(PTPN...  PTPN11           G60D         not provided   
51   NM_002834.5(PTPN...  PTPN11           G60V  Noonan syndrome ...   
52   NM_002834.5(PTPN...  PTPN11           G60A  Noonan syndrome ...   
53   NM_002834.5(PTPN...  PTPN11           D61Y  not provided|Noo...   
54   NM_002834.5(PTPN...  PTPN11           D61N  PTPN11-rela

In [139]:
# Clean df_stat for analysis
df_stat = df_stat.dropna(subset=['REVEL', 'Germline classification']) # Keep only rows where REVEL or ClinVar classification is not NaN
df_stat['REVEL'] = pd.to_numeric(df_stat['REVEL'], errors='coerce') # Make sure REVEL is numeric
df_stat['Germline classification'] = df_stat['Germline classification'].astype(str).str.strip()

# Select only the columns needed for statistical classification
columns_to_keep = [
    'GRCh38Location',
    'GRCh37Location',
    'Protein change',
    'Germline classification',
    'REVEL',
    'BayesDel_noAF',
    'BayesDel_addAF',
    'AAfrom',
    'AAto',
    'AApos_ClinVar'
]

df_stat = df_stat[columns_to_keep]

# Quick check
print(df_stat.head())

   GRCh38Location GRCh37Location Protein change Germline classification  \
0       112419113      112856917            M1R    Likely pathogenic      
1       112419116      112856920            T2I  Pathogenic/Likel...      
2       112419121      112856925            R4G  Conflicting clas...      
3       112419122      112856926            R4Q    Likely pathogenic      
4       112446279      112884083            W6C  Uncertain signif...      

   REVEL  BayesDel_noAF  BayesDel_addAF AAfrom AAto  AApos_ClinVar  
0  0.202       0.660000        0.660000      M    R              1  
1  0.213       0.010807        0.010807      T    I              2  
2  0.518       0.044882        0.044882      R    G              4  
3  0.393      -0.022043       -0.022043      R    Q              4  
4  0.920       0.512606        0.512606      W    C              6  


In [140]:
# Save merged file
df_stat.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_ClinVar_REVEL_BayesDel.csv", index=False)


In [137]:
df_stat

GRCh38Location GRCh37Location Germline classification     REVEL  \
0         112419113      112856917    Likely pathogenic     0.202000   
1         112419116      112856920  Pathogenic/Likel...     0.213000   
2         112419121      112856925  Conflicting clas...     0.518000   
3         112419122      112856926    Likely pathogenic     0.393000   
4         112446279      112884083  Uncertain signif...     0.920000   
5         112446279      112884083  Uncertain signif...     0.920000   
6         112446289      112884093  Uncertain signif...     0.703000   
7         112446289      112884093  Uncertain signif...     0.436000   
8         112446289      112884093  Uncertain signif...     0.372000   
9         112446290      112884094  Uncertain signif...     0.471000   
10        112446290      112884094  Uncertain signif...     0.396000   
11        112446293      112884097  Uncertain signif...     0.883000   
12        112446295      112884099  Uncertain signif...     0.509000   
13        112446301      112884105  Uncertain signif...     0.375000   
14        112446313      112884117  Uncertain signif...     0.308000   
15        112446314      112884118               Benign     0.301000   
16        112446316      112884120  Uncertain signif...     0.598000   
17        112446325      112884129  Uncertain signif...     0.374000   
18        112446332      112884136  Uncertain signif...     0.751000   
19        112446341      112884145  Uncertain signif...     0.941000   
20        112446352      112884156  Uncertain signif...     0.778000   
21        112446353      112884157    Likely pathogenic     0.720000   
22        112446364      112884168  Uncertain signif...     0.369000   
23        112446364      112884168  Uncertain signif...     0.251000   
24        112446365      112884169  Uncertain signif...     0.599000   
25        112446376      112884180  Uncertain signif...     0.919500   
26        112446380      112884184  Uncertain signif...     0.684000   
27        112446385      112884189    Likely pathogenic     0.612000   
28        112446385      112884189           Pathogenic     0.794000   
29        112446388      112884192  Uncertain signif...     0.822000   
30        112446388      112884192  Conflicting clas...     0.924000   
31        112446394      112884198  Uncertain signif...     0.565000   
32        112450325      112888129  Uncertain signif...     0.814000   
33        112450328      112888132  Uncertain signif...     0.312000   
34        112450335      112888139  Uncertain signif...     0.673000   
35        112450335      112888139           Pathogenic     0.912000   
36        112450344      112888148  Uncertain signif...     0.545000   
37        112450346      112888150           Pathogenic     0.772000   
38        112450347      112888151    Likely pathogenic     0.969000   
39        112450351      112888155    Likely pathogenic     0.760000   
40        112450352      112888156  Pathogenic/Likel...     0.897000   
41        112450352      112888156           Pathogenic     0.757000   
42        112450352      112888156           Pathogenic     0.760000   
43        112450353      112888157  Conflicting clas...     0.610000   
44        112450354      112888158  Pathogenic/Likel...     0.589000   
45        112450354      112888158           Pathogenic     0.589000   
46        112450355      112888159  Conflicting clas...     0.707000   
47        112450358      112888162  Pathogenic/Likel...     0.937000   
48        112450358      112888162  Pathogenic/Likel...     0.952000   
49        112450358      112888162  Pathogenic/Likel...     0.890000   
50        112450359      112888163    Likely pathogenic     0.842000   
51        112450359      112888163  Pathogenic/Likel...     0.931000   
52        112450359      112888163           Pathogenic     0.907000   
53        112450361      112888165  Conflicting clas...     0.933000   
54        112450361      112888165           